In [1]:
import numpy as np # library to handle data in a vectorized manner
import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

import requests

from bs4 import BeautifulSoup

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    ca-certificates-2020.4.5.1 |       hecc5488_0         146 KB  conda-forge
    geopy-1.21.0               |             py_0          58 KB  conda-forge
    certifi-2020.4.5.1         |   py36h9f0ad1d_0         151 KB  conda-forge
    python_abi-3.6             |          1_cp36m           4 KB  conda-forge
    geographiclib-1.50         |             py_0          34 KB  conda-forge
    openssl-1.1.1g             |       h516909a_0         2.1 MB  conda-forge
    ------------------------------------------------------------
                                           Total:         2.5 MB

The following NEW packages will be INSTALLED:

    geographiclib:   1.50-py_0         conda-forge
    geopy:           1

In [ ]:
# These take time so do them after all the data extraction part

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
#import folium # map rendering library

## Extract Data

### Pop density data

In [2]:
req1 = requests.get("https://en.wikipedia.org/wiki/Template:NYC_boroughs")

soup = BeautifulSoup(req1.content,'lxml')

table = soup.find_all('table')[0]

popden = pd.read_html(str(table))

popden = pd.DataFrame(popden[0])

popden

New York City's five boroughsvte  \
                                      Jurisdiction   
                                           Borough   
0                                        The Bronx   
1                                         Brooklyn   
2                                        Manhattan   
3                                           Queens   
4                                    Staten Island   
5                                 City of New York   
6                                State of New York   
7  Sources:[3] and see individual borough articles   

                                                    \
                                                     
                                            County   
0                                            Bronx   
1                                            Kings   
2                                         New York   
3                                           Queens   
4                                         Richmond   
5                                 City of New York   
6                                State of New York   
7  Sources:[3] and see individual borough articles   

                                                    \
                                        Population   
                                Estimate (2018)[1]   
0                                          1432132   
1                                          2582830   
2                                          1628701   
3                                          2278906   
4                                           476179   
5                                          8398748   
6                                         19745289   
7  Sources:[3] and see individual borough articles   

                                                    \
                            Gross Domestic Product   
                                  billions(US$)[2]   
0                                           42.695   
1                                           91.559   
2                                          600.244   
3                                           93.310   
4                                           14.514   
5                                          842.343   
6                                         1701.399   
7  Sources:[3] and see individual borough articles   

                                                    \
                                                     
                                   per capita(US$)   
0                                            29200   
1                                            34600   
2                                           360900   
3                                            39600   
4                                            30300   
5                                            97700   
6                                            85700   
7  Sources:[3] and see individual borough articles   

                                                    \
                                         Land area   
                                      square miles   
0                                            42.10   
1                                            70.82   
2                                            22.83   
3                                           108.53   
4                                            58.37   
5                                           302.64   
6                                            47214   
7  Sources:[3] and see individual borough articles   

                                                    \
                                                     
                                          squarekm   
0                                           109.04   
1                                           183.42   
2                                            59.13   
3                                           281.09   
4                                           151.18   
5               

In [3]:
popden.columns

MultiIndex(levels=[['New York City's five boroughsvte'], ['Density', 'Gross Domestic Product', 'Jurisdiction', 'Land area', 'Population'], ['Borough', 'County', 'Estimate (2018)[1]', 'billions(US$)[2]', 'per capita(US$)', 'persons / sq. mi', 'persons /km2', 'square miles', 'squarekm']],
           codes=[[0, 0, 0, 0, 0, 0, 0, 0, 0], [2, 2, 4, 1, 1, 3, 3, 0, 0], [0, 1, 2, 3, 4, 7, 8, 5, 6]])

In [4]:
popden = popden.drop(index=[5,6,7])

In [5]:
popden = popden.drop(columns=['County', 'Estimate (2018)[1]', 'billions(US$)[2]', 'per capita(US$)','square miles', 'squarekm' ], level=2)
popden

New York City's five boroughsvte                              
                      Jurisdiction          Density             
                           Borough persons / sq. mi persons /km2
0                        The Bronx            34653        13231
1                         Brooklyn            37137        14649
2                        Manhattan            72033        27826
3                           Queens            21460         8354
4                    Staten Island             8112         3132

In [7]:
#Run this code twice to remove the highest 2 levels
popden.columns = popden.columns.droplevel(0)
popden

Borough persons / sq. mi persons /km2
0      The Bronx            34653        13231
1       Brooklyn            37137        14649
2      Manhattan            72033        27826
3         Queens            21460         8354
4  Staten Island             8112         3132

In [8]:
popden = popden.rename(columns={'persons / sq. mi':'pkm', 'persons /km2': 'pmi'})
popden.set_value(0, 'Borough', 'Bronx')
popden

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:2: FutureWarning: set_value is deprecated and will be removed in a future release. Please use .at[] or .iat[] accessors instead
  from ipykernel import kernelapp as app


Borough    pkm    pmi
0          Bronx  34653  13231
1       Brooklyn  37137  14649
2      Manhattan  72033  27826
3         Queens  21460   8354
4  Staten Island   8112   3132

In [9]:
popden.dtypes

Borough    object
pkm        object
pmi        object
dtype: object

In [10]:
popden['Borough'] = popden['Borough'].astype(str)
popden.pkm = popden.pkm.astype(int)
popden.pmi = popden.pmi.astype(int)
print(popden.dtypes)
popden

Borough    object
pkm         int64
pmi         int64
dtype: object


Borough    pkm    pmi
0          Bronx  34653  13231
1       Brooklyn  37137  14649
2      Manhattan  72033  27826
3         Queens  21460   8354
4  Staten Island   8112   3132

### Extract zipcode

In [11]:
req2 = requests.get("https://www.health.ny.gov/statistics/cancer/registry/appendix/neighborhoods.htm")

soup1 = BeautifulSoup(req2.content,'lxml')

table1 = soup1.find_all('table')[0]

zipco = pd.read_html(str(table1))

zipco =pd.DataFrame(zipco[0])

zipco

Borough                   Neighborhood  \
0           Bronx                  Central Bronx   
1           Bronx         Bronx Park and Fordham   
2           Bronx     High Bridge and Morrisania   
3           Bronx     Hunts Point and Mott Haven   
4           Bronx      Kingsbridge and Riverdale   
5           Bronx                Northeast Bronx   
6           Bronx                Southeast Bronx   
7        Brooklyn               Central Brooklyn   
8        Brooklyn             Southwest Brooklyn   
9        Brooklyn                   Borough Park   
10       Brooklyn         Canarsie and Flatlands   
11       Brooklyn              Southern Brooklyn   
12       Brooklyn             Northwest Brooklyn   
13       Brooklyn                       Flatbush   
14       Brooklyn     East New York and New Lots   
15       Brooklyn                     Greenpoint   
16       Brooklyn                    Sunset Park   
17       Brooklyn      Bushwick and Williamsburg   
18      Manhattan                 Central Harlem   
19      Manhattan            Chelsea and Clinton   
20      Manhattan                    East Harlem   
21      Manhattan  Gramercy Park and Murray Hill   
22      Manhattan     Greenwich Village and Soho   
23      Manhattan                Lower Manhattan   
24      Manhattan                Lower East Side   
25      Manhattan                Upper East Side   
26      Manhattan                Upper West Side   
27      Manhattan  Inwood and Washington Heights   
28         Queens               Northeast Queens   
29         Queens                   North Queens   
30         Queens                 Central Queens   
31         Queens                        Jamaica   
32         Queens               Northwest Queens   
33         Queens            West Central Queens   
34         Queens                      Rockaways   
35         Queens               Southeast Queens   
36         Queens               Southwest Queens   
37         Queens                    West Queens   
38  Staten Island                  Port Richmond   
39  Staten Island                    South Shore   
40  Staten Island       Stapleton and St. George   
41  Staten Island                     Mid-Island   

                                            ZIP Codes  
0                                 10453, 10457, 10460  
1                                 10458, 10467, 10468  
2                                 10451, 10452, 10456  
3                          10454, 10455, 10459, 10474  
4                                        10463, 10471  
5                          10466, 10469, 10470, 10475  
6             10461, 10462,10464, 10465, 10472, 10473  
7                   11212, 11213, 11216, 11233, 11238  
8                                 11209, 11214, 11228  
9                          11204, 11218, 11219, 11230  
10                                11234, 11236, 11239  
11                         11223, 11224, 11229, 11235  
12                  11201, 11205, 11215, 11217, 11231  
13                         11203, 11210, 11225, 11226  
14                                       11207, 11208  
15                                       11211, 11222  
16                                       11220, 11232  
17                                11206, 11221, 11237  
18                  10026, 10027, 10030, 10037, 10039  
19           10001, 10011, 10018, 10019, 10020, 10036  
20                                       10029, 10035  
21                         10010, 10016, 10017, 10022  
22                                10012, 10013, 10014  
23           10004, 10005, 10006, 10007, 10038, 10280  
24                                10002, 10003, 10009  
25           10021, 10028, 10044, 10065, 10075, 10128  
26                                10023, 10024, 10025  
27                  10031, 10032, 10033, 10034, 10040  
28                         11361, 11362, 11363, 11364  
29    11354, 11355, 11356, 11357, 11358, 11359, 11360  
30                                113

In [12]:
zipco = zipco.rename(columns={'ZIP Codes': 'ZIPCODE'})
zipco.dtypes

Borough         object
Neighborhood    object
ZIPCODE         object
dtype: object

In [13]:
zipco.Borough = zipco.Borough.astype(str)
zipco.Neighborhood = zipco.Neighborhood.astype(str)
zipco.ZIPCODE = zipco.ZIPCODE.astype(str)
zipco.dtypes

Borough         object
Neighborhood    object
ZIPCODE         object
dtype: object

In [14]:
zipco = pd.concat([zipco,zipco.ZIPCODE.str.split(',',expand=True)],1)

In [15]:
zipco = zipco.drop(columns='ZIPCODE')

In [16]:
print(zipco.columns)
zipco

Index(['Borough', 'Neighborhood', 0, 1, 2, 3, 4, 5, 6, 7, 8], dtype='object')


Borough                   Neighborhood      0       1       2  \
0           Bronx                  Central Bronx  10453   10457   10460   
1           Bronx         Bronx Park and Fordham  10458   10467   10468   
2           Bronx     High Bridge and Morrisania  10451   10452   10456   
3           Bronx     Hunts Point and Mott Haven  10454   10455   10459   
4           Bronx      Kingsbridge and Riverdale  10463   10471    None   
5           Bronx                Northeast Bronx  10466   10469   10470   
6           Bronx                Southeast Bronx  10461   10462   10464   
7        Brooklyn               Central Brooklyn  11212   11213   11216   
8        Brooklyn             Southwest Brooklyn  11209   11214   11228   
9        Brooklyn                   Borough Park  11204   11218   11219   
10       Brooklyn         Canarsie and Flatlands  11234   11236   11239   
11       Brooklyn              Southern Brooklyn  11223   11224   11229   
12       Brooklyn             Northwest Brooklyn  11201   11205   11215   
13       Brooklyn                       Flatbush  11203   11210   11225   
14       Brooklyn     East New York and New Lots  11207   11208    None   
15       Brooklyn                     Greenpoint  11211   11222    None   
16       Brooklyn                    Sunset Park  11220   11232    None   
17       Brooklyn      Bushwick and Williamsburg  11206   11221   11237   
18      Manhattan                 Central Harlem  10026   10027   10030   
19      Manhattan            Chelsea and Clinton  10001   10011   10018   
20      Manhattan                    East Harlem  10029   10035    None   
21      Manhattan  Gramercy Park and Murray Hill  10010   10016   10017   
22      Manhattan     Greenwich Village and Soho  10012   10013   10014   
23      Manhattan                Lower Manhattan  10004   10005   10006   
24      Manhattan                Lower East Side  10002   10003   10009   
25      Manhattan                Upper East Side  10021   10028   10044   
26      Manhattan                Upper West Side  10023   10024   10025   
27      Manhattan  Inwood and Washington Heights  10031   10032   10033   
28         Queens               Northeast Queens  11361   11362   11363   
29         Queens                   North Queens  11354   11355   11356   
30         Queens                 Central Queens  11365   11366   11367   
31         Queens                        Jamaica  11412   11423   11432   
32         Queens               Northwest Queens  11101   11102   11103   
33         Queens            West Central Queens  11374   11375   11379   
34         Queens                      Rockaways  11691   11692   11693   
35         Queens               Southeast Queens  11004   11005   11411   
36         Queens               Southwest Queens  11414   11415   11416   
37         Queens                    West Queens  11368   11369   11370   
38  Staten Island                  Port Richmond  10302   10303   10310   
39  Staten Island                    South Shore  10306   10307   10308   
40  Staten Island       Stapleton and St. George  10301   10304   10305   
41  Staten Island                     Mid-Island  10314    None    None   

         3       4       5       6       7       8  
0     None    None    None    None    None    None  
1     None    None    None    None    None    None  
2     None    None    None    None    None    None  
3    10474    None    None    None    None    None  
4     None    None    None    None    None    None  
5    10475    None    None    None    None    None  
6    10465   10472   10473    None    None    None  
7    11233   11238    None    None    None    None  
8     None    None    None    None    None    None  
9    11230    None    None    None    None    None  
10    None    None    None    None    None    None  
11   11235    None    None    None    None    None  
12   11217   11231    None    None    None    None  
13   11226    None    None    None    None

In [17]:
z1 = zipco.set_index(['Borough', 'Neighborhood'])
z1 = z1.stack(0,1).reset_index()
z1

Borough                   Neighborhood  level_2       0
0            Bronx                  Central Bronx        0   10453
1            Bronx                  Central Bronx        1   10457
2            Bronx                  Central Bronx        2   10460
3            Bronx         Bronx Park and Fordham        0   10458
4            Bronx         Bronx Park and Fordham        1   10467
5            Bronx         Bronx Park and Fordham        2   10468
6            Bronx     High Bridge and Morrisania        0   10451
7            Bronx     High Bridge and Morrisania        1   10452
8            Bronx     High Bridge and Morrisania        2   10456
9            Bronx     Hunts Point and Mott Haven        0   10454
10           Bronx     Hunts Point and Mott Haven        1   10455
11           Bronx     Hunts Point and Mott Haven        2   10459
12           Bronx     Hunts Point and Mott Haven        3   10474
13           Bronx      Kingsbridge and Riverdale        0   10463
14           Bronx      Kingsbridge and Riverdale        1   10471
15           Bronx                Northeast Bronx        0   10466
16           Bronx                Northeast Bronx        1   10469
17           Bronx                Northeast Bronx        2   10470
18           Bronx                Northeast Bronx        3   10475
19           Bronx                Southeast Bronx        0   10461
20           Bronx                Southeast Bronx        1   10462
21           Bronx                Southeast Bronx        2   10464
22           Bronx                Southeast Bronx        3   10465
23           Bronx                Southeast Bronx        4   10472
24           Bronx                Southeast Bronx        5   10473
25        Brooklyn               Central Brooklyn        0   11212
26        Brooklyn               Central Brooklyn        1   11213
27        Brooklyn               Central Brooklyn        2   11216
28        Brooklyn               Central Brooklyn        3   11233
29        Brooklyn               Central Brooklyn        4   11238
30        Brooklyn             Southwest Brooklyn        0   11209
31        Brooklyn             Southwest Brooklyn        1   11214
32        Brooklyn             Southwest Brooklyn        2   11228
33        Brooklyn                   Borough Park        0   11204
34        Brooklyn                   Borough Park        1   11218
35        Brooklyn                   Borough Park        2   11219
36        Brooklyn                   Borough Park        3   11230
37        Brooklyn         Canarsie and Flatlands        0   11234
38        Brooklyn         Canarsie and Flatlands        1   11236
39        Brooklyn         Canarsie and Flatlands        2   11239
40        Brooklyn              Southern Brooklyn        0   11223
41        Brooklyn              Southern Brooklyn        1   11224
42        Brooklyn              Southern Brooklyn        2   11229
43        Brooklyn              Southern Brooklyn        3   11235
44        Brooklyn             Northwest Brooklyn        0   11201
45        Brooklyn             Northwest Brooklyn        1   11205
46        Brooklyn             Northwest Brooklyn        2   11215
47        Brooklyn             Northwest Brooklyn        3   11217
48        Brooklyn             Northwest Brooklyn        4   11231
49        Brooklyn                       Flatbush        0   11203
50        Brooklyn                       Flatbush        1   11210
51        Brooklyn                       Flatbush        2   11225
52        Brooklyn                       Flatbush        3   11226
53        Brooklyn     East New York and New Lots        0   11207
54        Brooklyn     East New York and New Lots        1   11208
55        Brooklyn                     Greenpoint        0   11211
56        Brooklyn                     Greenpoint        1   11222
57        Brooklyn                    Sunset Park        0   11220
58        Brooklyn                    Sunset Park        1

In [18]:
z1 = z1.drop(columns='level_2')
z1.rename(columns={0: 'ZIPCODES'}, inplace=True)
z1

Borough                   Neighborhood ZIPCODES
0            Bronx                  Central Bronx    10453
1            Bronx                  Central Bronx    10457
2            Bronx                  Central Bronx    10460
3            Bronx         Bronx Park and Fordham    10458
4            Bronx         Bronx Park and Fordham    10467
5            Bronx         Bronx Park and Fordham    10468
6            Bronx     High Bridge and Morrisania    10451
7            Bronx     High Bridge and Morrisania    10452
8            Bronx     High Bridge and Morrisania    10456
9            Bronx     Hunts Point and Mott Haven    10454
10           Bronx     Hunts Point and Mott Haven    10455
11           Bronx     Hunts Point and Mott Haven    10459
12           Bronx     Hunts Point and Mott Haven    10474
13           Bronx      Kingsbridge and Riverdale    10463
14           Bronx      Kingsbridge and Riverdale    10471
15           Bronx                Northeast Bronx    10466
16           Bronx                Northeast Bronx    10469
17           Bronx                Northeast Bronx    10470
18           Bronx                Northeast Bronx    10475
19           Bronx                Southeast Bronx    10461
20           Bronx                Southeast Bronx    10462
21           Bronx                Southeast Bronx    10464
22           Bronx                Southeast Bronx    10465
23           Bronx                Southeast Bronx    10472
24           Bronx                Southeast Bronx    10473
25        Brooklyn               Central Brooklyn    11212
26        Brooklyn               Central Brooklyn    11213
27        Brooklyn               Central Brooklyn    11216
28        Brooklyn               Central Brooklyn    11233
29        Brooklyn               Central Brooklyn    11238
30        Brooklyn             Southwest Brooklyn    11209
31        Brooklyn             Southwest Brooklyn    11214
32        Brooklyn             Southwest Brooklyn    11228
33        Brooklyn                   Borough Park    11204
34        Brooklyn                   Borough Park    11218
35        Brooklyn                   Borough Park    11219
36        Brooklyn                   Borough Park    11230
37        Brooklyn         Canarsie and Flatlands    11234
38        Brooklyn         Canarsie and Flatlands    11236
39        Brooklyn         Canarsie and Flatlands    11239
40        Brooklyn              Southern Brooklyn    11223
41        Brooklyn              Southern Brooklyn    11224
42        Brooklyn              Southern Brooklyn    11229
43        Brooklyn              Southern Brooklyn    11235
44        Brooklyn             Northwest Brooklyn    11201
45        Brooklyn             Northwest Brooklyn    11205
46        Brooklyn             Northwest Brooklyn    11215
47        Brooklyn             Northwest Brooklyn    11217
48        Brooklyn             Northwest Brooklyn    11231
49        Brooklyn                       Flatbush    11203
50        Brooklyn                       Flatbush    11210
51        Brooklyn                       Flatbush    11225
52        Brooklyn                       Flatbush    11226
53        Brooklyn     East New York and New Lots    11207
54        Brooklyn     East New York and New Lots    11208
55        Brooklyn                     Greenpoint    11211
56        Brooklyn                     Greenpoint    11222
57        Brooklyn                    Sunset Park    11220
58        Brooklyn                    Sunset Park    11232
59        Brooklyn      Bushwick and Williamsburg    11206
60        Brooklyn      Bushwick and Williamsburg    11221
61        Brooklyn      Bushwick and Williamsburg    11237
62       Manhattan                 Central Harlem    10026
63       Manhattan                 Central Harlem    10027
64       Manhattan                 Central Harlem    10030
65       Manhattan                 Central Harlem    10037
66       Manhattan                 Central Harlem    10039

### Corona cases by zip code then transformed to per Borough/Neighborhood

In [19]:
req3 = requests.get("https://github.com/nychealth/coronavirus-data/blob/master/tests-by-zcta.csv")

soup2 = BeautifulSoup(req3.content,'lxml')

table2 = soup2.find_all('table')[0]

cor = pd.read_html(str(table2))

cor =pd.DataFrame(cor[0])

cor

Unnamed: 0  MODZCTA  Positive  Total  zcta_cum.perc_pos
0           NaN      NaN      1845   2073              89.00
1           NaN  10001.0       266    600              44.33
2           NaN  10002.0       729   1419              51.37
3           NaN  10003.0       355    857              41.42
4           NaN  10004.0        26     66              39.39
5           NaN  10005.0        44    140              31.43
6           NaN  10006.0        15     58              25.86
7           NaN  10007.0        42    142              29.58
8           NaN  10009.0       530   1230              43.09
9           NaN  10010.0       203    591              34.35
10          NaN  10011.0       403    892              45.18
11          NaN  10012.0       121    345              35.07
12          NaN  10013.0       180    439              41.00
13          NaN  10014.0       236    543              43.46
14          NaN  10016.0       515   1258              40.94
15          NaN  10017.0       109    327              33.33
16          NaN  10018.0       169    384              44.01
17          NaN  10019.0       449   1032              43.51
18          NaN  10021.0       438   1179              37.15
19          NaN  10022.0       254    698              36.39
20          NaN  10023.0       439   1152              38.11
21          NaN  10024.0       484   1284              37.69
22          NaN  10025.0       901   2088              43.15
23          NaN  10026.0       443    899              49.28
24          NaN  10027.0       667   1290              51.71
25          NaN  10028.0       379   1035              36.62
26          NaN  10029.0      1202   2340              51.37
27          NaN  10030.0       360    623              57.78
28          NaN  10031.0       841   1351              62.25
29          NaN  10032.0       968   1636              59.17
30          NaN  10033.0       817   1348              60.61
31          NaN  10034.0       458    851              53.82
32          NaN  10035.0       664   1167              56.90
33          NaN  10036.0       309    694              44.52
34          NaN  10037.0       304    559              54.38
35          NaN  10038.0       171    363              47.11
36          NaN  10039.0       339    650              52.15
37          NaN  10040.0       644   1051              61.27
38          NaN  10044.0       124    266              46.62
39          NaN  10065.0       252    764              32.98
40          NaN  10069.0        45    119              37.82
41          NaN  10075.0       309    706              43.77
42          NaN  10128.0       501   1367              36.65
43          NaN  10280.0        33    108              30.56
44          NaN  10282.0        58    119              48.74
45          NaN  10301.0       848   1736              48.85
46          NaN  10302.0       450    919              48.97
47          NaN  10303.0       638   1292              49.38
48          NaN  10304.0      1035   2128              48.64
49          NaN  10305.0       914   2128              42.95
50          NaN  10306.0      1124   2807              40.04
51          NaN  10307.0       311    734              42.37
52          NaN  10308.0       519   1325              39.17
53          NaN  10309.0       688   1734              39.68
54          NaN  10310.0       534   1232              43.34
55          NaN  10312.0      1224   2820              43.40
56          NaN  10314.0      2030   4551              44.61
57          NaN  10451.0      1108   1938              57.17
58          NaN  10452.0      1488   2440              60.98
59          NaN  10453.0      1547   2622              59.00
60          NaN  10454.0       747   1272              58.73
61          NaN  10455.0       831   1435              57.91
62          NaN  10456.0      1596   2738              58.29
63          NaN  10457.0      1362   2319              58.73
64          NaN  10458.0      1342   243

In [20]:
cor = cor.drop(columns=['Unnamed: 0', 'Total','zcta_cum.perc_pos'])
cor = cor.rename(columns={'MODZCTA':'ZIPCODES'})
cor = cor.drop(index=0)
cor

ZIPCODES  Positive
1     10001.0       266
2     10002.0       729
3     10003.0       355
4     10004.0        26
5     10005.0        44
6     10006.0        15
7     10007.0        42
8     10009.0       530
9     10010.0       203
10    10011.0       403
11    10012.0       121
12    10013.0       180
13    10014.0       236
14    10016.0       515
15    10017.0       109
16    10018.0       169
17    10019.0       449
18    10021.0       438
19    10022.0       254
20    10023.0       439
21    10024.0       484
22    10025.0       901
23    10026.0       443
24    10027.0       667
25    10028.0       379
26    10029.0      1202
27    10030.0       360
28    10031.0       841
29    10032.0       968
30    10033.0       817
31    10034.0       458
32    10035.0       664
33    10036.0       309
34    10037.0       304
35    10038.0       171
36    10039.0       339
37    10040.0       644
38    10044.0       124
39    10065.0       252
40    10069.0        45
41    10075.0       309
42    10128.0       501
43    10280.0        33
44    10282.0        58
45    10301.0       848
46    10302.0       450
47    10303.0       638
48    10304.0      1035
49    10305.0       914
50    10306.0      1124
51    10307.0       311
52    10308.0       519
53    10309.0       688
54    10310.0       534
55    10312.0      1224
56    10314.0      2030
57    10451.0      1108
58    10452.0      1488
59    10453.0      1547
60    10454.0       747
61    10455.0       831
62    10456.0      1596
63    10457.0      1362
64    10458.0      1342
65    10459.0       996
66    10460.0      1097
67    10461.0      1328
68    10462.0      1611
69    10463.0      1261
70    10464.0       103
71    10465.0      1128
72    10466.0      1727
73    10467.0      2372
74    10468.0      1666
75    10469.0      2131
76    10470.0       336
77    10471.0       414
78    10472.0      1287
79    10473.0      1371
80    10474.0       230
81    10475.0      1285
82    11004.0       415
83    11101.0       440
84    11102.0       405
85    11103.0       377
86    11104.0       330
87    11105.0       357
88    11106.0       431
89    11109.0        41
90    11201.0       460
91    11203.0      1385
92    11204.0      1358
93    11205.0       490
94    11206.0      1013
95    11207.0      1306
96    11208.0      1463
97    11209.0       800
98    11210.0      1219
99    11211.0      1422
100   11212.0      1134
101   11213.0      1010
102   11214.0      1050
103   11215.0       453
104   11216.0       500
105   11217.0       411
106   11218.0      1192
107   11219.0      1988
108   11220.0      1025
109   11221.0       832
110   11222.0       316
111   11223.0      1171
112   11224.0       695
113   11225.0       843
114   11226.0      1413
115   11228.0       470
116   11229.0      1110
117   11230.0      1620
118   11231.0       303
119   11232.0       351
120   11233.0       844
121   11234.0      1670
122   11235.0      1343
123   11236.0      1899
124   11237.0       590
125   11238.0       547
126   11239.0       354
127   11354.0       714
128   11355.0       822
129   11356.0       376
130   11357.0       580
131   11358.0       395
132   11360.0       215
133   11361.0       317
134   11362.0       220
135   11363.0        76
136   11364.0       343
137   11365.0       585
138   11366.0       306
139   11367.0       712
140   11368.0      2919
141   11369.0      1081
142   11370.0      1037
143   11372.0      1764
144   11373.0      2269
145   11374.0       817
146   11375.0      1170
147   11377.0      1448
148   11378.0       509
149   11379.0       558
150   11385.0      1396
151   11411.0       503
152   11412.0       900
153   11413.0       954
154   11414.0       618
155   11415.0       377
156   11416.0       438
157   11417.0       573
158   11418.0       702
159   11419.0       753
160   11420.0       914
161   11421.0       804
162   11422.0       707
163   11423.0       688
164   11426.0       366
165   11427.0       566
166   11428.0       4

In [21]:
cor.ZIPCODES = cor.ZIPCODES.astype(str)

In [22]:
cor

ZIPCODES  Positive
1    10001.0       266
2    10002.0       729
3    10003.0       355
4    10004.0        26
5    10005.0        44
6    10006.0        15
7    10007.0        42
8    10009.0       530
9    10010.0       203
10   10011.0       403
11   10012.0       121
12   10013.0       180
13   10014.0       236
14   10016.0       515
15   10017.0       109
16   10018.0       169
17   10019.0       449
18   10021.0       438
19   10022.0       254
20   10023.0       439
21   10024.0       484
22   10025.0       901
23   10026.0       443
24   10027.0       667
25   10028.0       379
26   10029.0      1202
27   10030.0       360
28   10031.0       841
29   10032.0       968
30   10033.0       817
31   10034.0       458
32   10035.0       664
33   10036.0       309
34   10037.0       304
35   10038.0       171
36   10039.0       339
37   10040.0       644
38   10044.0       124
39   10065.0       252
40   10069.0        45
41   10075.0       309
42   10128.0       501
43   10280.0        33
44   10282.0        58
45   10301.0       848
46   10302.0       450
47   10303.0       638
48   10304.0      1035
49   10305.0       914
50   10306.0      1124
51   10307.0       311
52   10308.0       519
53   10309.0       688
54   10310.0       534
55   10312.0      1224
56   10314.0      2030
57   10451.0      1108
58   10452.0      1488
59   10453.0      1547
60   10454.0       747
61   10455.0       831
62   10456.0      1596
63   10457.0      1362
64   10458.0      1342
65   10459.0       996
66   10460.0      1097
67   10461.0      1328
68   10462.0      1611
69   10463.0      1261
70   10464.0       103
71   10465.0      1128
72   10466.0      1727
73   10467.0      2372
74   10468.0      1666
75   10469.0      2131
76   10470.0       336
77   10471.0       414
78   10472.0      1287
79   10473.0      1371
80   10474.0       230
81   10475.0      1285
82   11004.0       415
83   11101.0       440
84   11102.0       405
85   11103.0       377
86   11104.0       330
87   11105.0       357
88   11106.0       431
89   11109.0        41
90   11201.0       460
91   11203.0      1385
92   11204.0      1358
93   11205.0       490
94   11206.0      1013
95   11207.0      1306
96   11208.0      1463
97   11209.0       800
98   11210.0      1219
99   11211.0      1422
100  11212.0      1134
101  11213.0      1010
102  11214.0      1050
103  11215.0       453
104  11216.0       500
105  11217.0       411
106  11218.0      1192
107  11219.0      1988
108  11220.0      1025
109  11221.0       832
110  11222.0       316
111  11223.0      1171
112  11224.0       695
113  11225.0       843
114  11226.0      1413
115  11228.0       470
116  11229.0      1110
117  11230.0      1620
118  11231.0       303
119  11232.0       351
120  11233.0       844
121  11234.0      1670
122  11235.0      1343
123  11236.0      1899
124  11237.0       590
125  11238.0       547
126  11239.0       354
127  11354.0       714
128  11355.0       822
129  11356.0       376
130  11357.0       580
131  11358.0       395
132  11360.0       215
133  11361.0       317
134  11362.0       220
135  11363.0        76
136  11364.0       343
137  11365.0       585
138  11366.0       306
139  11367.0       712
140  11368.0      2919
141  11369.0      1081
142  11370.0      1037
143  11372.0      1764
144  11373.0      2269
145  11374.0       817
146  11375.0      1170
147  11377.0      1448
148  11378.0       509
149  11379.0       558
150  11385.0      1396
151  11411.0       503
152  11412.0       900
153  11413.0       954
154  11414.0       618
155  11415.0       377
156  11416.0       438
157  11417.0       573
158  11418.0       702
159  11419.0       753
160  11420.0       914
161  11421.0       804
162  11422.0       707
163  11423.0       688
164  11426.0       366
165  11427.0       566
166  11428.0       489
167  11429.0       690
168  11432.0      1133
169  11433.0       643
170  11434.0      1415
171  11435.0      1057
172  11436.0       357
173  11691.0      1543
17

### MERGE ALL TABLES (VERY TRICKY STEP)

In [23]:
print(popden.shape)
print(z1.shape)
print(cor.shape)

(5, 3)
(178, 3)
(177, 2)


In [24]:
cor.ZIPCODES = cor.ZIPCODES.astype(float)
z1.ZIPCODES = z1.ZIPCODES.astype(float)

In [25]:
# Join Corona by zipcode to the zipcode table
tt1 = pd.merge(z1, cor, on='ZIPCODES', sort=False)
tt1

Borough                   Neighborhood  ZIPCODES  Positive
0            Bronx                  Central Bronx   10453.0      1547
1            Bronx                  Central Bronx   10457.0      1362
2            Bronx                  Central Bronx   10460.0      1097
3            Bronx         Bronx Park and Fordham   10458.0      1342
4            Bronx         Bronx Park and Fordham   10467.0      2372
5            Bronx         Bronx Park and Fordham   10468.0      1666
6            Bronx     High Bridge and Morrisania   10451.0      1108
7            Bronx     High Bridge and Morrisania   10452.0      1488
8            Bronx     High Bridge and Morrisania   10456.0      1596
9            Bronx     Hunts Point and Mott Haven   10454.0       747
10           Bronx     Hunts Point and Mott Haven   10455.0       831
11           Bronx     Hunts Point and Mott Haven   10459.0       996
12           Bronx     Hunts Point and Mott Haven   10474.0       230
13           Bronx      Kingsbridge and Riverdale   10463.0      1261
14           Bronx      Kingsbridge and Riverdale   10471.0       414
15           Bronx                Northeast Bronx   10466.0      1727
16           Bronx                Northeast Bronx   10469.0      2131
17           Bronx                Northeast Bronx   10470.0       336
18           Bronx                Northeast Bronx   10475.0      1285
19           Bronx                Southeast Bronx   10461.0      1328
20           Bronx                Southeast Bronx   10462.0      1611
21           Bronx                Southeast Bronx   10464.0       103
22           Bronx                Southeast Bronx   10465.0      1128
23           Bronx                Southeast Bronx   10472.0      1287
24           Bronx                Southeast Bronx   10473.0      1371
25        Brooklyn               Central Brooklyn   11212.0      1134
26        Brooklyn               Central Brooklyn   11213.0      1010
27        Brooklyn               Central Brooklyn   11216.0       500
28        Brooklyn               Central Brooklyn   11233.0       844
29        Brooklyn               Central Brooklyn   11238.0       547
30        Brooklyn             Southwest Brooklyn   11209.0       800
31        Brooklyn             Southwest Brooklyn   11214.0      1050
32        Brooklyn             Southwest Brooklyn   11228.0       470
33        Brooklyn                   Borough Park   11204.0      1358
34        Brooklyn                   Borough Park   11218.0      1192
35        Brooklyn                   Borough Park   11219.0      1988
36        Brooklyn                   Borough Park   11230.0      1620
37        Brooklyn         Canarsie and Flatlands   11234.0      1670
38        Brooklyn         Canarsie and Flatlands   11236.0      1899
39        Brooklyn         Canarsie and Flatlands   11239.0       354
40        Brooklyn              Southern Brooklyn   11223.0      1171
41        Brooklyn              Southern Brooklyn   11224.0       695
42        Brooklyn              Southern Brooklyn   11229.0      1110
43        Brooklyn              Southern Brooklyn   11235.0      1343
44        Brooklyn             Northwest Brooklyn   11201.0       460
45        Brooklyn             Northwest Brooklyn   11205.0       490
46        Brooklyn             Northwest Brooklyn   11215.0       453
47        Brooklyn             Northwest Brooklyn   11217.0       411
48        Brooklyn             Northwest Brooklyn   11231.0       303
49        Brooklyn                       Flatbush   11203.0      1385
50        Brooklyn                       Flatbush   11210.0      1219
51        Brooklyn                       Flatbush   11225.0       843
52        Brooklyn                       Flatbush   11226.0      1413
53        Brooklyn     East New York and New Lots   11207.0      1306
54        Brooklyn     East New York and New Lots   11208.0      1463
55        Brooklyn                     Greenpoint   11211.0      1422
56        Brooklyn   

In [26]:
# merge the density table
tt2 = pd.merge(tt1, popden, on='Borough', sort=False)
print(tt2.shape)
print(len(tt2['ZIPCODES'].unique()))
tt2

(174, 6)
174


Borough                   Neighborhood  ZIPCODES  Positive    pkm  \
0            Bronx                  Central Bronx   10453.0      1547  34653   
1            Bronx                  Central Bronx   10457.0      1362  34653   
2            Bronx                  Central Bronx   10460.0      1097  34653   
3            Bronx         Bronx Park and Fordham   10458.0      1342  34653   
4            Bronx         Bronx Park and Fordham   10467.0      2372  34653   
5            Bronx         Bronx Park and Fordham   10468.0      1666  34653   
6            Bronx     High Bridge and Morrisania   10451.0      1108  34653   
7            Bronx     High Bridge and Morrisania   10452.0      1488  34653   
8            Bronx     High Bridge and Morrisania   10456.0      1596  34653   
9            Bronx     Hunts Point and Mott Haven   10454.0       747  34653   
10           Bronx     Hunts Point and Mott Haven   10455.0       831  34653   
11           Bronx     Hunts Point and Mott Haven   10459.0       996  34653   
12           Bronx     Hunts Point and Mott Haven   10474.0       230  34653   
13           Bronx      Kingsbridge and Riverdale   10463.0      1261  34653   
14           Bronx      Kingsbridge and Riverdale   10471.0       414  34653   
15           Bronx                Northeast Bronx   10466.0      1727  34653   
16           Bronx                Northeast Bronx   10469.0      2131  34653   
17           Bronx                Northeast Bronx   10470.0       336  34653   
18           Bronx                Northeast Bronx   10475.0      1285  34653   
19           Bronx                Southeast Bronx   10461.0      1328  34653   
20           Bronx                Southeast Bronx   10462.0      1611  34653   
21           Bronx                Southeast Bronx   10464.0       103  34653   
22           Bronx                Southeast Bronx   10465.0      1128  34653   
23           Bronx                Southeast Bronx   10472.0      1287  34653   
24           Bronx                Southeast Bronx   10473.0      1371  34653   
25        Brooklyn               Central Brooklyn   11212.0      1134  37137   
26        Brooklyn               Central Brooklyn   11213.0      1010  37137   
27        Brooklyn               Central Brooklyn   11216.0       500  37137   
28        Brooklyn               Central Brooklyn   11233.0       844  37137   
29        Brooklyn               Central Brooklyn   11238.0       547  37137   
30        Brooklyn             Southwest Brooklyn   11209.0       800  37137   
31        Brooklyn             Southwest Brooklyn   11214.0      1050  37137   
32        Brooklyn             Southwest Brooklyn   11228.0       470  37137   
33        Brooklyn                   Borough Park   11204.0      1358  37137   
34        Brooklyn                   Borough Park   11218.0      1192  37137   
35        Brooklyn                   Borough Park   11219.0      1988  37137   
36        Brooklyn                   Borough Park   11230.0      1620  37137   
37        Brooklyn         Canarsie and Flatlands   11234.0      1670  37137   
38        Brooklyn         Canarsie and Flatlands   11236.0      1899  37137   
39        Brooklyn         Canarsie and Flatlands   11239.0       354  37137   
40        Brooklyn              Southern Brooklyn   11223.0      1171  37137   
41        Brooklyn              Southern Brooklyn   11224.0       695  37137   
42        Brooklyn              Southern Brooklyn   11229.0      1110  37137   
43        Brooklyn              Southern Brooklyn   11235.0      1343  37137   
44        Brooklyn             Northwest Brooklyn   11201.0       460  37137   
45        Brooklyn             Northwest Brooklyn   11205.0       490  37137   
46        Brooklyn             Northwest Brooklyn   11215.0       453  37137   
47        Brooklyn             Northwest Brooklyn   11217.0       411  37137   
48        Brooklyn             Northwest Brooklyn   11231.0       303  37137   
49        B

### Get the coordinates of every ZIPCODE

In [59]:

body = client_58ab1ccf43ec4d8ab6e0f6f057690320.get_object(Bucket='capstonecourse-donotdelete-pr-0x6sjxe1pbh7ue',Key='us-zip-code-latitude-and-longitude.csv')['Body']
# add missing __iter__ method, so pandas accepts body as file-like object
if not hasattr(body, "__iter__"): body.__iter__ = types.MethodType( __iter__, body )

df_data_2 = pd.read_csv(body)
df_data_2.head()
coor = df_data_2.reset_index()
coor

index  \
0      14043;Depew;NY;42.904958;-78.7006;-5;1;42.904958   
1     13827;Owego;NY;42.120274;-76.25874;-5;1;42.120274   
2     14739;Friendship;NY;42.192384;-78.14308;-5;1;4...   
3     11703;North Babylon;NY;40.733398;-73.32257;-5;...   
4     11707;West Babylon;NY;40.922326;-72.637078;-5;...   
5     12442;Hunter;NY;42.222061;-74.23418;-5;1;42.22...   
6       13334;Eaton;NY;42.83917;-75.65482;-5;1;42.83917   
7     13626;Copenhagen;NY;43.859025;-75.72942;-5;1;4...   
8     10965;Pearl River;NY;41.063329;-74.01734;-5;1;...   
9     12151;Round Lake;NY;42.932326;-73.79363;-5;1;4...   
10    12195;West Lebanon;NY;42.479384;-73.474809;-5;...   
11    14617;Rochester;NY;43.223213;-77.59721;-5;1;43...   
12    11716;Bohemia;NY;40.770042;-73.11376;-5;1;40.7...   
13    12719;Barryville;NY;41.480326;-74.92694;-5;1;4...   
14    13479;Washington Mills;NY;43.053769;-75.271559...   
15    10072;New York;NY;40.780751;-73.977182;-5;1;40...   
16    10166;New York;NY;40.754591;-73.976238;-5;1;40...   
17    10998;Westtown;NY;41.334034;-74.54593;-5;1;41....   
18    11560;Locust Valley;NY;40.881957;-73.59417;-5;...   
19    14150;Tonawanda;NY;43.001907;-78.8631;-5;1;43....   
20    12197;Worcester;NY;42.610314;-74.72401;-5;1;42...   
21    13147;Scipio Center;NY;42.774714;-76.57045;-5;...   
22    12771;Port Jervis;NY;41.374734;-74.66315;-5;1;...   
23    12810;Athol;NY;43.484741;-73.89151;-5;1;43.484741   
24    13350;Herkimer;NY;43.038149;-74.9846;-5;1;43.0...   
25    13655;Hogansburg;NY;44.98184;-74.67374;-5;1;44...   
26    13788;Hobart;NY;42.368357;-74.66452;-5;1;42.36...   
27    14717;Caneadea;NY;42.37074;-78.19335;-5;1;42.3...   
28    13459;Sharon Springs;NY;42.774077;-74.58404;-5...   
29    14642;Rochester;NY;43.286024;-77.684264;-5;1;4...   
30    10986;Tomkins Cove;NY;41.271543;-73.98676;-5;1...   
31    11763;Medford;NY;40.820786;-72.98375;-5;1;40.8...   
32     12139;Piseco;NY;43.40276;-74.56972;-5;1;43.40276   
33    12509;La Grange;NY;41.643599;-73.847176;-5;1;4...   
34    13503;Utica;NY;43.101869;-75.231158;-5;1;43.10...   
35    13135;Phoenix;NY;43.235916;-76.31339;-5;1;43.2...   
36    14301;Niagara Falls;NY;43.096555;-79.03925;-5;...   
37    13082;Kirkville;NY;43.099547;-75.9619;-5;1;43....   
38    10506;Bedford;NY;41.195778;-73.62777;-5;1;41.1...   
39    13312;Brantingham;NY;43.689564;-75.27252;-5;1;...   
40    12789;Woodridge;NY;41.708062;-74.5698;-5;1;41....   
41    14472;Honeoye Falls;NY;42.964593;-77.5919;-5;1...   
42    11783;Seaford;NY;40.679752;-73.48959;-5;1;40.6...   
43    12245;Albany;NY;42.614852;-73.970812;-5;1;42.6...   
44    12861;Putnam Station;NY;43.74531;-73.41569;-5;...   
45    13860;West Davenport;NY;42.183045;-74.925617;-...   
46    14612;Rochester;NY;43.256462;-77.66183;-5;1;43...   
47    13840;Smithboro;NY;42.039512;-76.400376;-5;1;4...   
48    14754;Little Genesee;NY;42.020028;-78.20368;-5...   
49    14901;Elmira;NY;42.091924;-76.79217;-5;1;42.09...   
50    12305;Schenectady;NY;42.814476;-73.94337;-5;1;...   
51    12402;Kingston;NY;41.878801;-74.345684;-5;1;41...   
52    13843;South New Berlin;NY;42.533274;-75.38008;...   
53    10607;White Plains;NY;41.041191;-73.80953;-5;1...   
54    13664;Morristown;NY;44.585561;-75.64797;-5;1;4...   
55    14482;Le Roy;NY;42.979887;-77.97053;-5;1;42.97...   
56    14214;Buffalo;NY;42.941407;-78.83741;-5;1;42.9...   
57    10268;New York;NY;40.780751;-73.977182;-5;1;40...   
58    10917;Central Valley;NY;41.322344;-74.12354;-5...   
59    12784;Thompsonville;NY;41.676139;-74.6217;-5;1...   
60    13104;Manlius;NY;42.987329;-75.96763;-5;1;42.9...   
61    13208;Syracuse;NY;43.074566;-76.14747;-5;1;43....   
62    10547;Mohegan Lake;NY;41.314676;-73.85118;-5;1...   
63    11937;East Hampton;NY;40.995384;-72.18564;-5;1...   
64    12527;Glenham;NY;41.520249;-73.933259;-5;1;41....   
65    13658;Lisbon;NY;44.744462;-75.28123;-5;1;44.74...   
66    13688;South Rutland;NY;43.951666;-75.767772;-5...   
67    14138;South Dayton;NY;42.372077;

In [60]:
coor.index = coor.index.astype(str)
coor = coor.rename(columns={'index':"one"})
coor

one  \
0      14043;Depew;NY;42.904958;-78.7006;-5;1;42.904958   
1     13827;Owego;NY;42.120274;-76.25874;-5;1;42.120274   
2     14739;Friendship;NY;42.192384;-78.14308;-5;1;4...   
3     11703;North Babylon;NY;40.733398;-73.32257;-5;...   
4     11707;West Babylon;NY;40.922326;-72.637078;-5;...   
5     12442;Hunter;NY;42.222061;-74.23418;-5;1;42.22...   
6       13334;Eaton;NY;42.83917;-75.65482;-5;1;42.83917   
7     13626;Copenhagen;NY;43.859025;-75.72942;-5;1;4...   
8     10965;Pearl River;NY;41.063329;-74.01734;-5;1;...   
9     12151;Round Lake;NY;42.932326;-73.79363;-5;1;4...   
10    12195;West Lebanon;NY;42.479384;-73.474809;-5;...   
11    14617;Rochester;NY;43.223213;-77.59721;-5;1;43...   
12    11716;Bohemia;NY;40.770042;-73.11376;-5;1;40.7...   
13    12719;Barryville;NY;41.480326;-74.92694;-5;1;4...   
14    13479;Washington Mills;NY;43.053769;-75.271559...   
15    10072;New York;NY;40.780751;-73.977182;-5;1;40...   
16    10166;New York;NY;40.754591;-73.976238;-5;1;40...   
17    10998;Westtown;NY;41.334034;-74.54593;-5;1;41....   
18    11560;Locust Valley;NY;40.881957;-73.59417;-5;...   
19    14150;Tonawanda;NY;43.001907;-78.8631;-5;1;43....   
20    12197;Worcester;NY;42.610314;-74.72401;-5;1;42...   
21    13147;Scipio Center;NY;42.774714;-76.57045;-5;...   
22    12771;Port Jervis;NY;41.374734;-74.66315;-5;1;...   
23    12810;Athol;NY;43.484741;-73.89151;-5;1;43.484741   
24    13350;Herkimer;NY;43.038149;-74.9846;-5;1;43.0...   
25    13655;Hogansburg;NY;44.98184;-74.67374;-5;1;44...   
26    13788;Hobart;NY;42.368357;-74.66452;-5;1;42.36...   
27    14717;Caneadea;NY;42.37074;-78.19335;-5;1;42.3...   
28    13459;Sharon Springs;NY;42.774077;-74.58404;-5...   
29    14642;Rochester;NY;43.286024;-77.684264;-5;1;4...   
30    10986;Tomkins Cove;NY;41.271543;-73.98676;-5;1...   
31    11763;Medford;NY;40.820786;-72.98375;-5;1;40.8...   
32     12139;Piseco;NY;43.40276;-74.56972;-5;1;43.40276   
33    12509;La Grange;NY;41.643599;-73.847176;-5;1;4...   
34    13503;Utica;NY;43.101869;-75.231158;-5;1;43.10...   
35    13135;Phoenix;NY;43.235916;-76.31339;-5;1;43.2...   
36    14301;Niagara Falls;NY;43.096555;-79.03925;-5;...   
37    13082;Kirkville;NY;43.099547;-75.9619;-5;1;43....   
38    10506;Bedford;NY;41.195778;-73.62777;-5;1;41.1...   
39    13312;Brantingham;NY;43.689564;-75.27252;-5;1;...   
40    12789;Woodridge;NY;41.708062;-74.5698;-5;1;41....   
41    14472;Honeoye Falls;NY;42.964593;-77.5919;-5;1...   
42    11783;Seaford;NY;40.679752;-73.48959;-5;1;40.6...   
43    12245;Albany;NY;42.614852;-73.970812;-5;1;42.6...   
44    12861;Putnam Station;NY;43.74531;-73.41569;-5;...   
45    13860;West Davenport;NY;42.183045;-74.925617;-...   
46    14612;Rochester;NY;43.256462;-77.66183;-5;1;43...   
47    13840;Smithboro;NY;42.039512;-76.400376;-5;1;4...   
48    14754;Little Genesee;NY;42.020028;-78.20368;-5...   
49    14901;Elmira;NY;42.091924;-76.79217;-5;1;42.09...   
50    12305;Schenectady;NY;42.814476;-73.94337;-5;1;...   
51    12402;Kingston;NY;41.878801;-74.345684;-5;1;41...   
52    13843;South New Berlin;NY;42.533274;-75.38008;...   
53    10607;White Plains;NY;41.041191;-73.80953;-5;1...   
54    13664;Morristown;NY;44.585561;-75.64797;-5;1;4...   
55    14482;Le Roy;NY;42.979887;-77.97053;-5;1;42.97...   
56    14214;Buffalo;NY;42.941407;-78.83741;-5;1;42.9...   
57    10268;New York;NY;40.780751;-73.977182;-5;1;40...   
58    10917;Central Valley;NY;41.322344;-74.12354;-5...   
59    12784;Thompsonville;NY;41.676139;-74.6217;-5;1...   
60    13104;Manlius;NY;42.987329;-75.96763;-5;1;42.9...   
61    13208;Syracuse;NY;43.074566;-76.14747;-5;1;43....   
62    10547;Mohegan Lake;NY;41.314676;-73.85118;-5;1...   
63    11937;East Hampton;NY;40.995384;-72.18564;-5;1...   
64    12527;Glenham;NY;41.520249;-73.933259;-5;1;41....   
65    13658;Lisbon;NY;44.744462;-75.28123;-5;1;44.74...   
66    13688;South Rutland;NY;43.951666;-75.767772;-5...   
67    14138;South Dayton;NY;42.372077;-7

In [61]:
coor = pd.concat([coor,coor.one.str.split(';',expand=True)],1)
coor

one  \
0      14043;Depew;NY;42.904958;-78.7006;-5;1;42.904958   
1     13827;Owego;NY;42.120274;-76.25874;-5;1;42.120274   
2     14739;Friendship;NY;42.192384;-78.14308;-5;1;4...   
3     11703;North Babylon;NY;40.733398;-73.32257;-5;...   
4     11707;West Babylon;NY;40.922326;-72.637078;-5;...   
5     12442;Hunter;NY;42.222061;-74.23418;-5;1;42.22...   
6       13334;Eaton;NY;42.83917;-75.65482;-5;1;42.83917   
7     13626;Copenhagen;NY;43.859025;-75.72942;-5;1;4...   
8     10965;Pearl River;NY;41.063329;-74.01734;-5;1;...   
9     12151;Round Lake;NY;42.932326;-73.79363;-5;1;4...   
10    12195;West Lebanon;NY;42.479384;-73.474809;-5;...   
11    14617;Rochester;NY;43.223213;-77.59721;-5;1;43...   
12    11716;Bohemia;NY;40.770042;-73.11376;-5;1;40.7...   
13    12719;Barryville;NY;41.480326;-74.92694;-5;1;4...   
14    13479;Washington Mills;NY;43.053769;-75.271559...   
15    10072;New York;NY;40.780751;-73.977182;-5;1;40...   
16    10166;New York;NY;40.754591;-73.976238;-5;1;40...   
17    10998;Westtown;NY;41.334034;-74.54593;-5;1;41....   
18    11560;Locust Valley;NY;40.881957;-73.59417;-5;...   
19    14150;Tonawanda;NY;43.001907;-78.8631;-5;1;43....   
20    12197;Worcester;NY;42.610314;-74.72401;-5;1;42...   
21    13147;Scipio Center;NY;42.774714;-76.57045;-5;...   
22    12771;Port Jervis;NY;41.374734;-74.66315;-5;1;...   
23    12810;Athol;NY;43.484741;-73.89151;-5;1;43.484741   
24    13350;Herkimer;NY;43.038149;-74.9846;-5;1;43.0...   
25    13655;Hogansburg;NY;44.98184;-74.67374;-5;1;44...   
26    13788;Hobart;NY;42.368357;-74.66452;-5;1;42.36...   
27    14717;Caneadea;NY;42.37074;-78.19335;-5;1;42.3...   
28    13459;Sharon Springs;NY;42.774077;-74.58404;-5...   
29    14642;Rochester;NY;43.286024;-77.684264;-5;1;4...   
30    10986;Tomkins Cove;NY;41.271543;-73.98676;-5;1...   
31    11763;Medford;NY;40.820786;-72.98375;-5;1;40.8...   
32     12139;Piseco;NY;43.40276;-74.56972;-5;1;43.40276   
33    12509;La Grange;NY;41.643599;-73.847176;-5;1;4...   
34    13503;Utica;NY;43.101869;-75.231158;-5;1;43.10...   
35    13135;Phoenix;NY;43.235916;-76.31339;-5;1;43.2...   
36    14301;Niagara Falls;NY;43.096555;-79.03925;-5;...   
37    13082;Kirkville;NY;43.099547;-75.9619;-5;1;43....   
38    10506;Bedford;NY;41.195778;-73.62777;-5;1;41.1...   
39    13312;Brantingham;NY;43.689564;-75.27252;-5;1;...   
40    12789;Woodridge;NY;41.708062;-74.5698;-5;1;41....   
41    14472;Honeoye Falls;NY;42.964593;-77.5919;-5;1...   
42    11783;Seaford;NY;40.679752;-73.48959;-5;1;40.6...   
43    12245;Albany;NY;42.614852;-73.970812;-5;1;42.6...   
44    12861;Putnam Station;NY;43.74531;-73.41569;-5;...   
45    13860;West Davenport;NY;42.183045;-74.925617;-...   
46    14612;Rochester;NY;43.256462;-77.66183;-5;1;43...   
47    13840;Smithboro;NY;42.039512;-76.400376;-5;1;4...   
48    14754;Little Genesee;NY;42.020028;-78.20368;-5...   
49    14901;Elmira;NY;42.091924;-76.79217;-5;1;42.09...   
50    12305;Schenectady;NY;42.814476;-73.94337;-5;1;...   
51    12402;Kingston;NY;41.878801;-74.345684;-5;1;41...   
52    13843;South New Berlin;NY;42.533274;-75.38008;...   
53    10607;White Plains;NY;41.041191;-73.80953;-5;1...   
54    13664;Morristown;NY;44.585561;-75.64797;-5;1;4...   
55    14482;Le Roy;NY;42.979887;-77.97053;-5;1;42.97...   
56    14214;Buffalo;NY;42.941407;-78.83741;-5;1;42.9...   
57    10268;New York;NY;40.780751;-73.977182;-5;1;40...   
58    10917;Central Valley;NY;41.322344;-74.12354;-5...   
59    12784;Thompsonville;NY;41.676139;-74.6217;-5;1...   
60    13104;Manlius;NY;42.987329;-75.96763;-5;1;42.9...   
61    13208;Syracuse;NY;43.074566;-76.14747;-5;1;43....   
62    10547;Mohegan Lake;NY;41.314676;-73.85118;-5;1...   
63    11937;East Hampton;NY;40.995384;-72.18564;-5;1...   
64    12527;Glenham;NY;41.520249;-73.933259;-5;1;41....   
65    13658;Lisbon;NY;44.744462;-75.28123;-5;1;44.74...   
66    13688;South Rutland;NY;43.951666;-75.767772;-5...   
67    14138;South Dayton;NY;42.372077;-7

In [62]:
coor1 = coor[[0,3,4]]
coor1

0                   3                   4
0     14043           42.904958            -78.7006
1     13827           42.120274           -76.25874
2     14739           42.192384           -78.14308
3     11703           40.733398           -73.32257
4     11707           40.922326          -72.637078
5     12442           42.222061           -74.23418
6     13334            42.83917           -75.65482
7     13626           43.859025           -75.72942
8     10965           41.063329           -74.01734
9     12151           42.932326           -73.79363
10    12195           42.479384          -73.474809
11    14617           43.223213           -77.59721
12    11716           40.770042           -73.11376
13    12719           41.480326           -74.92694
14    13479           43.053769          -75.271559
15    10072           40.780751          -73.977182
16    10166           40.754591          -73.976238
17    10998           41.334034           -74.54593
18    11560           40.881957           -73.59417
19    14150           43.001907            -78.8631
20    12197           42.610314           -74.72401
21    13147           42.774714           -76.57045
22    12771           41.374734           -74.66315
23    12810           43.484741           -73.89151
24    13350           43.038149            -74.9846
25    13655            44.98184           -74.67374
26    13788           42.368357           -74.66452
27    14717            42.37074           -78.19335
28    13459           42.774077           -74.58404
29    14642           43.286024          -77.684264
30    10986           41.271543           -73.98676
31    11763           40.820786           -72.98375
32    12139            43.40276           -74.56972
33    12509           41.643599          -73.847176
34    13503           43.101869          -75.231158
35    13135           43.235916           -76.31339
36    14301           43.096555           -79.03925
37    13082           43.099547            -75.9619
38    10506           41.195778           -73.62777
39    13312           43.689564           -75.27252
40    12789           41.708062            -74.5698
41    14472           42.964593            -77.5919
42    11783           40.679752           -73.48959
43    12245           42.614852          -73.970812
44    12861            43.74531           -73.41569
45    13860           42.183045          -74.925617
46    14612           43.256462           -77.66183
47    13840           42.039512          -76.400376
48    14754           42.020028           -78.20368
49    14901           42.091924           -76.79217
50    12305           42.814476           -73.94337
51    12402           41.878801          -74.345684
52    13843           42.533274           -75.38008
53    10607           41.041191           -73.80953
54    13664           44.585561           -75.64797
55    14482           42.979887           -77.97053
56    14214           42.941407           -78.83741
57    10268           40.780751          -73.977182
58    10917           41.322344           -74.12354
59    12784           41.676139            -74.6217
60    13104           42.987329           -75.96763
61    13208           43.074566           -76.14747
62    10547           41.314676           -73.85118
63    11937           40.995384           -72.18564
64    12527           41.520249          -73.933259
65    13658           44.744462           -75.28123
66    13688           43.951666          -75.767772
67    14138           42.372077           -79.05552
68    12233           42.614852          -73.970812
69    12515           41.681096           -74.06421
70    13638           44.021094           -75.76113
71    14054           42.903676           -78.13481
72    13333           42.843048           -74.80882
73    13820           42.469761           -75.05192
74    14437           42.576771           -77.71925
75    14506           42.999201           -77.50263
76    

In [63]:
print (~coor1.columns.duplicated())

[ True  True  True]


In [57]:
coor1 = coor1.loc[:, ~coor1.columns.duplicated()]

In [64]:
coor1

0                   3                   4
0     14043           42.904958            -78.7006
1     13827           42.120274           -76.25874
2     14739           42.192384           -78.14308
3     11703           40.733398           -73.32257
4     11707           40.922326          -72.637078
5     12442           42.222061           -74.23418
6     13334            42.83917           -75.65482
7     13626           43.859025           -75.72942
8     10965           41.063329           -74.01734
9     12151           42.932326           -73.79363
10    12195           42.479384          -73.474809
11    14617           43.223213           -77.59721
12    11716           40.770042           -73.11376
13    12719           41.480326           -74.92694
14    13479           43.053769          -75.271559
15    10072           40.780751          -73.977182
16    10166           40.754591          -73.976238
17    10998           41.334034           -74.54593
18    11560           40.881957           -73.59417
19    14150           43.001907            -78.8631
20    12197           42.610314           -74.72401
21    13147           42.774714           -76.57045
22    12771           41.374734           -74.66315
23    12810           43.484741           -73.89151
24    13350           43.038149            -74.9846
25    13655            44.98184           -74.67374
26    13788           42.368357           -74.66452
27    14717            42.37074           -78.19335
28    13459           42.774077           -74.58404
29    14642           43.286024          -77.684264
30    10986           41.271543           -73.98676
31    11763           40.820786           -72.98375
32    12139            43.40276           -74.56972
33    12509           41.643599          -73.847176
34    13503           43.101869          -75.231158
35    13135           43.235916           -76.31339
36    14301           43.096555           -79.03925
37    13082           43.099547            -75.9619
38    10506           41.195778           -73.62777
39    13312           43.689564           -75.27252
40    12789           41.708062            -74.5698
41    14472           42.964593            -77.5919
42    11783           40.679752           -73.48959
43    12245           42.614852          -73.970812
44    12861            43.74531           -73.41569
45    13860           42.183045          -74.925617
46    14612           43.256462           -77.66183
47    13840           42.039512          -76.400376
48    14754           42.020028           -78.20368
49    14901           42.091924           -76.79217
50    12305           42.814476           -73.94337
51    12402           41.878801          -74.345684
52    13843           42.533274           -75.38008
53    10607           41.041191           -73.80953
54    13664           44.585561           -75.64797
55    14482           42.979887           -77.97053
56    14214           42.941407           -78.83741
57    10268           40.780751          -73.977182
58    10917           41.322344           -74.12354
59    12784           41.676139            -74.6217
60    13104           42.987329           -75.96763
61    13208           43.074566           -76.14747
62    10547           41.314676           -73.85118
63    11937           40.995384           -72.18564
64    12527           41.520249          -73.933259
65    13658           44.744462           -75.28123
66    13688           43.951666          -75.767772
67    14138           42.372077           -79.05552
68    12233           42.614852          -73.970812
69    12515           41.681096           -74.06421
70    13638           44.021094           -75.76113
71    14054           42.903676           -78.13481
72    13333           42.843048           -74.80882
73    13820           42.469761           -75.05192
74    14437           42.576771           -77.71925
75    14506           42.999201           -77.50263
76    

In [65]:
coor1 = coor1.rename(columns={0:'ZIPCODES', 3:'lat', 4:'long'})
coor1

ZIPCODES                 lat                long
0       14043           42.904958            -78.7006
1       13827           42.120274           -76.25874
2       14739           42.192384           -78.14308
3       11703           40.733398           -73.32257
4       11707           40.922326          -72.637078
5       12442           42.222061           -74.23418
6       13334            42.83917           -75.65482
7       13626           43.859025           -75.72942
8       10965           41.063329           -74.01734
9       12151           42.932326           -73.79363
10      12195           42.479384          -73.474809
11      14617           43.223213           -77.59721
12      11716           40.770042           -73.11376
13      12719           41.480326           -74.92694
14      13479           43.053769          -75.271559
15      10072           40.780751          -73.977182
16      10166           40.754591          -73.976238
17      10998           41.334034           -74.54593
18      11560           40.881957           -73.59417
19      14150           43.001907            -78.8631
20      12197           42.610314           -74.72401
21      13147           42.774714           -76.57045
22      12771           41.374734           -74.66315
23      12810           43.484741           -73.89151
24      13350           43.038149            -74.9846
25      13655            44.98184           -74.67374
26      13788           42.368357           -74.66452
27      14717            42.37074           -78.19335
28      13459           42.774077           -74.58404
29      14642           43.286024          -77.684264
30      10986           41.271543           -73.98676
31      11763           40.820786           -72.98375
32      12139            43.40276           -74.56972
33      12509           41.643599          -73.847176
34      13503           43.101869          -75.231158
35      13135           43.235916           -76.31339
36      14301           43.096555           -79.03925
37      13082           43.099547            -75.9619
38      10506           41.195778           -73.62777
39      13312           43.689564           -75.27252
40      12789           41.708062            -74.5698
41      14472           42.964593            -77.5919
42      11783           40.679752           -73.48959
43      12245           42.614852          -73.970812
44      12861            43.74531           -73.41569
45      13860           42.183045          -74.925617
46      14612           43.256462           -77.66183
47      13840           42.039512          -76.400376
48      14754           42.020028           -78.20368
49      14901           42.091924           -76.79217
50      12305           42.814476           -73.94337
51      12402           41.878801          -74.345684
52      13843           42.533274           -75.38008
53      10607           41.041191           -73.80953
54      13664           44.585561           -75.64797
55      14482           42.979887           -77.97053
56      14214           42.941407           -78.83741
57      10268           40.780751          -73.977182
58      10917           41.322344           -74.12354
59      12784           41.676139            -74.6217
60      13104           42.987329           -75.96763
61      13208           43.074566           -76.14747
62      10547           41.314676           -73.85118
63      11937           40.995384           -72.18564
64      12527           41.520249          -73.933259
65      13658           44.744462           -75.28123
66      13688           43.951666          -75.767772
67      14138           42.372077           -79.05552
68      12233           42.614852          -73.970812
69      12515           41.681096           -74.06421
70      13638           44.021094           -75.76113
71      14054           42.903676           -78.13481
72      13333           42.843048           -74.80882
73      1

## Join the coordinates to the main data table

In [67]:
coor1.ZIPCODES = coor1.ZIPCODES.astype(float)
NYCCOR = pd.merge(tt2, coor1, on='ZIPCODES', sort=False)
NYCCOR

Borough                   Neighborhood  ZIPCODES  Positive    pkm  \
0            Bronx                  Central Bronx   10453.0      1547  34653   
1            Bronx                  Central Bronx   10457.0      1362  34653   
2            Bronx                  Central Bronx   10460.0      1097  34653   
3            Bronx         Bronx Park and Fordham   10458.0      1342  34653   
4            Bronx         Bronx Park and Fordham   10467.0      2372  34653   
5            Bronx         Bronx Park and Fordham   10468.0      1666  34653   
6            Bronx     High Bridge and Morrisania   10451.0      1108  34653   
7            Bronx     High Bridge and Morrisania   10452.0      1488  34653   
8            Bronx     High Bridge and Morrisania   10456.0      1596  34653   
9            Bronx     Hunts Point and Mott Haven   10454.0       747  34653   
10           Bronx     Hunts Point and Mott Haven   10455.0       831  34653   
11           Bronx     Hunts Point and Mott Haven   10459.0       996  34653   
12           Bronx     Hunts Point and Mott Haven   10474.0       230  34653   
13           Bronx      Kingsbridge and Riverdale   10463.0      1261  34653   
14           Bronx      Kingsbridge and Riverdale   10471.0       414  34653   
15           Bronx                Northeast Bronx   10466.0      1727  34653   
16           Bronx                Northeast Bronx   10469.0      2131  34653   
17           Bronx                Northeast Bronx   10470.0       336  34653   
18           Bronx                Northeast Bronx   10475.0      1285  34653   
19           Bronx                Southeast Bronx   10461.0      1328  34653   
20           Bronx                Southeast Bronx   10462.0      1611  34653   
21           Bronx                Southeast Bronx   10464.0       103  34653   
22           Bronx                Southeast Bronx   10465.0      1128  34653   
23           Bronx                Southeast Bronx   10472.0      1287  34653   
24           Bronx                Southeast Bronx   10473.0      1371  34653   
25        Brooklyn               Central Brooklyn   11212.0      1134  37137   
26        Brooklyn               Central Brooklyn   11213.0      1010  37137   
27        Brooklyn               Central Brooklyn   11216.0       500  37137   
28        Brooklyn               Central Brooklyn   11233.0       844  37137   
29        Brooklyn               Central Brooklyn   11238.0       547  37137   
30        Brooklyn             Southwest Brooklyn   11209.0       800  37137   
31        Brooklyn             Southwest Brooklyn   11214.0      1050  37137   
32        Brooklyn             Southwest Brooklyn   11228.0       470  37137   
33        Brooklyn                   Borough Park   11204.0      1358  37137   
34        Brooklyn                   Borough Park   11218.0      1192  37137   
35        Brooklyn                   Borough Park   11219.0      1988  37137   
36        Brooklyn                   Borough Park   11230.0      1620  37137   
37        Brooklyn         Canarsie and Flatlands   11234.0      1670  37137   
38        Brooklyn         Canarsie and Flatlands   11236.0      1899  37137   
39        Brooklyn         Canarsie and Flatlands   11239.0       354  37137   
40        Brooklyn              Southern Brooklyn   11223.0      1171  37137   
41        Brooklyn              Southern Brooklyn   11224.0       695  37137   
42        Brooklyn              Southern Brooklyn   11229.0      1110  37137   
43        Brooklyn              Southern Brooklyn   11235.0      1343  37137   
44        Brooklyn             Northwest Brooklyn   11201.0       460  37137   
45        Brooklyn             Northwest Brooklyn   11205.0       490  37137   
46        Brooklyn             Northwest Brooklyn   11215.0       453  37137   
47        Brooklyn             Northwest Brooklyn   11217.0       411  37137   
48        Brooklyn             Northwest Brooklyn   11231.0       303  37137   
49        B

## Use FourSquare to extract information

In [69]:
CLIENT_ID = '0CKQ2FJAFNVTQU43MLBIHHJIV5GDAN0K5FN5CXHTJOWLNGEP' # your Foursquare ID
CLIENT_SECRET = 'IIL3JYNNCEI0AMPYTUMVQH3Z434UCBCMM3A4G5OFDWYVWRBN' # your Foursquare Secret
VERSION = '20180605'
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 0CKQ2FJAFNVTQU43MLBIHHJIV5GDAN0K5FN5CXHTJOWLNGEP
CLIENT_SECRET:IIL3JYNNCEI0AMPYTUMVQH3Z434UCBCMM3A4G5OFDWYVWRBN


In [71]:
radius = 500
LIMIT = 100

venues = []

for lat, long, post, borough, neighborhood in zip(NYCCOR['lat'], NYCCOR['long'], NYCCOR['ZIPCODES'], NYCCOR['Borough'], 
                                                  NYCCOR['Neighborhood']):
    url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            long, 
            radius, 
            LIMIT)
    
    results = requests.get(url).json()["response"]['groups'][0]['items']
    
    for venue in results:
        venues.append((
            post, 
            borough,
            neighborhood,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))

In [72]:
venues_df = pd.DataFrame(venues)


venues_df.columns = ['ZIPCODES', 'Borough', 'Neighborhood', 'BoroughLatitude', 'BoroughLongitude', 'VenueName', 'VenueLatitude', 'VenueLongitude', 'VenueCategory']

print(venues_df.shape)
venues_df.head()

(6933, 9)


ZIPCODES Borough   Neighborhood BoroughLatitude BoroughLongitude  \
0   10453.0   Bronx  Central Bronx       40.853017        -73.91214   
1   10453.0   Bronx  Central Bronx       40.853017        -73.91214   
2   10453.0   Bronx  Central Bronx       40.853017        -73.91214   
3   10453.0   Bronx  Central Bronx       40.853017        -73.91214   
4   10453.0   Bronx  Central Bronx       40.853017        -73.91214   

            VenueName  VenueLatitude  VenueLongitude       VenueCategory  
0     Accra Resturant      40.853871      -73.908421  African Restaurant  
1  Bravo Supermarkets      40.854107      -73.914162       Grocery Store  
2            Wingstop      40.854093      -73.907899         Wings Joint  
3   Papa John's Pizza      40.852429      -73.908976         Pizza Place  
4             Dunkin'      40.853669      -73.908844          Donut Shop

In [73]:
# one hot encoding
nyc_onehot = pd.get_dummies(venues_df[['VenueCategory']], prefix="", prefix_sep="")

# add postal, borough and neighborhood column back to dataframe
nyc_onehot['ZIPCODES'] = venues_df['ZIPCODES'] 
nyc_onehot['Borough'] = venues_df['Borough'] 
nyc_onehot['Neighborhoods'] = venues_df['Neighborhood'] 

# move zipcodes, borough and neighborhood column to the first column
fixed_columns = list(nyc_onehot.columns[-3:]) + list(nyc_onehot.columns[:-3])
nyc_onehot = nyc_onehot[fixed_columns]

print(nyc_onehot.shape)
nyc_onehot.head()

(6933, 392)


ZIPCODES Borough  Neighborhoods  Accessories Store  Acupuncturist  \
0   10453.0   Bronx  Central Bronx                  0              0   
1   10453.0   Bronx  Central Bronx                  0              0   
2   10453.0   Bronx  Central Bronx                  0              0   
3   10453.0   Bronx  Central Bronx                  0              0   
4   10453.0   Bronx  Central Bronx                  0              0   

   Adult Boutique  Afghan Restaurant  African Restaurant  Airport Terminal  \
0               0                  0                   1                 0   
1               0                  0                   0                 0   
2               0                  0                   0                 0   
3               0                  0                   0                 0   
4               0                  0                   0                 0   

   Airport Tram  American Restaurant  Animal Shelter  Antique Shop  Arcade  \
0             0                    0               0             0       0   
1             0                    0               0             0       0   
2             0                    0               0             0       0   
3             0                    0               0             0       0   
4             0                    0               0             0       0   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0                 0                       0            0           0   
1                 0                       0            0           0   
2                 0                       0            0           0   
3                 0                       0            0           0   
4                 0                       0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auditorium  \
0                    0                 0                   0           0   
1                    0                 0                   0           0   
2                    0                 0                   0           0   
3                    0                 0                   0           0   
4                    0                 0                   0           0   

   Australian Restaurant  Austrian Restaurant  Auto Workshop  Automotive Shop  \
0                      0                    0              0                0   
1                      0                    0              0                0   
2                      0                    0              0                0   
3                      0                    0              0                0   
4                      0                    0              0                0   

   BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0          0           0           0       0     0    0               0   
1          0           0           0       0     0    0               0   
2          0           0           0       0     0    0               0   
3          0           0           0       0     0    0               0   
4          0           0           0       0     0    0               0   

   Baseball Stadium  Basketball Court  Basketball Stadium  Beach  \
0                 0                 0                   0      0   
1                 0                 0                   0      0   
2                 0                 0                   0      0   
3                 0                 0                   0      0   
4                 0                 0                   0      0   

   Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  Big Box Store  \
0                0         0            0           0              0   
1                0         0            0           0              0   
2                0         0            0           0              0   
3                0         0            0           0              0   
4                0         0       

In [76]:
nyc_grouped = nyc_onehot.groupby(["ZIPCODES", "Borough", "Neighborhoods"]).mean().reset_index()

print(nyc_grouped.shape)
nyc_grouped

(171, 392)


ZIPCODES        Borough                  Neighborhoods  \
0     10001.0      Manhattan            Chelsea and Clinton   
1     10002.0      Manhattan                Lower East Side   
2     10003.0      Manhattan                Lower East Side   
3     10005.0      Manhattan                Lower Manhattan   
4     10006.0      Manhattan                Lower Manhattan   
5     10007.0      Manhattan                Lower Manhattan   
6     10009.0      Manhattan                Lower East Side   
7     10010.0      Manhattan  Gramercy Park and Murray Hill   
8     10011.0      Manhattan            Chelsea and Clinton   
9     10012.0      Manhattan     Greenwich Village and Soho   
10    10013.0      Manhattan     Greenwich Village and Soho   
11    10014.0      Manhattan     Greenwich Village and Soho   
12    10016.0      Manhattan  Gramercy Park and Murray Hill   
13    10017.0      Manhattan  Gramercy Park and Murray Hill   
14    10018.0      Manhattan            Chelsea and Clinton   
15    10019.0      Manhattan            Chelsea and Clinton   
16    10021.0      Manhattan                Upper East Side   
17    10022.0      Manhattan  Gramercy Park and Murray Hill   
18    10023.0      Manhattan                Upper West Side   
19    10024.0      Manhattan                Upper West Side   
20    10025.0      Manhattan                Upper West Side   
21    10026.0      Manhattan                 Central Harlem   
22    10027.0      Manhattan                 Central Harlem   
23    10028.0      Manhattan                Upper East Side   
24    10029.0      Manhattan                    East Harlem   
25    10030.0      Manhattan                 Central Harlem   
26    10031.0      Manhattan  Inwood and Washington Heights   
27    10032.0      Manhattan  Inwood and Washington Heights   
28    10033.0      Manhattan  Inwood and Washington Heights   
29    10034.0      Manhattan  Inwood and Washington Heights   
30    10035.0      Manhattan                    East Harlem   
31    10036.0      Manhattan            Chelsea and Clinton   
32    10037.0      Manhattan                 Central Harlem   
33    10038.0      Manhattan                Lower Manhattan   
34    10039.0      Manhattan                 Central Harlem   
35    10040.0      Manhattan  Inwood and Washington Heights   
36    10044.0      Manhattan                Upper East Side   
37    10128.0      Manhattan                Upper East Side   
38    10280.0      Manhattan                Lower Manhattan   
39    10301.0  Staten Island       Stapleton and St. George   
40    10302.0  Staten Island                  Port Richmond   
41    10303.0  Staten Island                  Port Richmond   
42    10304.0  Staten Island       Stapleton and St. George   
43    10305.0  Staten Island       Stapleton and St. George   
44    10306.0  Staten Island                    South Shore   
45    10307.0  Staten Island                    South Shore   
46    10308.0  Staten Island                    South Shore   
47    10309.0  Staten Island                    South Shore   
48    10310.0  Staten Island                  Port Richmond   
49    10312.0  Staten Island                    South Shore   
50    10314.0  Staten Island                     Mid-Island   
51    10451.0          Bronx     High Bridge and Morrisania   
52    10452.0          Bronx     High Bridge and Morrisania   
53    10453.0          Bronx                  Central Bronx   
54    10454.0          Bronx     Hunts Point and Mott Haven   
55    10455.0          Bronx     Hunts Point and Mott Haven   
56    10456.0          Bronx     High Bridge and Morrisania   
57    10457.0          Bronx                  Central Bronx   
58    10458.0          Bronx         Bronx Park and Fordham   
59    10459.0          Bronx     Hunts Point and Mott Haven   
60    10460.0          Bronx                  Central Bronx   
61    10461.0          Bronx                Southeast Bronx   
62    10462.0          Bronx        

In [78]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
areaColumns = ['ZIPCODES', 'Borough', 'Neighborhoods']
freqColumns = []
for ind in np.arange(num_top_venues):
    try:
        freqColumns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        freqColumns.append('{}th Most Common Venue'.format(ind+1))
columns = areaColumns+freqColumns

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['ZIPCODES'] = nyc_grouped['ZIPCODES']
neighborhoods_venues_sorted['Borough'] = nyc_grouped['Borough']
neighborhoods_venues_sorted['Neighborhoods'] = nyc_grouped['Neighborhoods']

for ind in np.arange(nyc_grouped.shape[0]):
    row_categories = nyc_grouped.iloc[ind, :].iloc[3:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    neighborhoods_venues_sorted.iloc[ind, 3:] = row_categories_sorted.index.values[0:num_top_venues]

# neighborhoods_venues_sorted.sort_values(freqColumns, inplace=True)
print(neighborhoods_venues_sorted.shape)
neighborhoods_venues_sorted

(171, 13)


ZIPCODES        Borough                  Neighborhoods  \
0     10001.0      Manhattan            Chelsea and Clinton   
1     10002.0      Manhattan                Lower East Side   
2     10003.0      Manhattan                Lower East Side   
3     10005.0      Manhattan                Lower Manhattan   
4     10006.0      Manhattan                Lower Manhattan   
5     10007.0      Manhattan                Lower Manhattan   
6     10009.0      Manhattan                Lower East Side   
7     10010.0      Manhattan  Gramercy Park and Murray Hill   
8     10011.0      Manhattan            Chelsea and Clinton   
9     10012.0      Manhattan     Greenwich Village and Soho   
10    10013.0      Manhattan     Greenwich Village and Soho   
11    10014.0      Manhattan     Greenwich Village and Soho   
12    10016.0      Manhattan  Gramercy Park and Murray Hill   
13    10017.0      Manhattan  Gramercy Park and Murray Hill   
14    10018.0      Manhattan            Chelsea and Clinton   
15    10019.0      Manhattan            Chelsea and Clinton   
16    10021.0      Manhattan                Upper East Side   
17    10022.0      Manhattan  Gramercy Park and Murray Hill   
18    10023.0      Manhattan                Upper West Side   
19    10024.0      Manhattan                Upper West Side   
20    10025.0      Manhattan                Upper West Side   
21    10026.0      Manhattan                 Central Harlem   
22    10027.0      Manhattan                 Central Harlem   
23    10028.0      Manhattan                Upper East Side   
24    10029.0      Manhattan                    East Harlem   
25    10030.0      Manhattan                 Central Harlem   
26    10031.0      Manhattan  Inwood and Washington Heights   
27    10032.0      Manhattan  Inwood and Washington Heights   
28    10033.0      Manhattan  Inwood and Washington Heights   
29    10034.0      Manhattan  Inwood and Washington Heights   
30    10035.0      Manhattan                    East Harlem   
31    10036.0      Manhattan            Chelsea and Clinton   
32    10037.0      Manhattan                 Central Harlem   
33    10038.0      Manhattan                Lower Manhattan   
34    10039.0      Manhattan                 Central Harlem   
35    10040.0      Manhattan  Inwood and Washington Heights   
36    10044.0      Manhattan                Upper East Side   
37    10128.0      Manhattan                Upper East Side   
38    10280.0      Manhattan                Lower Manhattan   
39    10301.0  Staten Island       Stapleton and St. George   
40    10302.0  Staten Island                  Port Richmond   
41    10303.0  Staten Island                  Port Richmond   
42    10304.0  Staten Island       Stapleton and St. George   
43    10305.0  Staten Island       Stapleton and St. George   
44    10306.0  Staten Island                    South Shore   
45    10307.0  Staten Island                    South Shore   
46    10308.0  Staten Island                    South Shore   
47    10309.0  Staten Island                    South Shore   
48    10310.0  Staten Island                  Port Richmond   
49    10312.0  Staten Island                    South Shore   
50    10314.0  Staten Island                     Mid-Island   
51    10451.0          Bronx     High Bridge and Morrisania   
52    10452.0          Bronx     High Bridge and Morrisania   
53    10453.0          Bronx                  Central Bronx   
54    10454.0          Bronx     Hunts Point and Mott Haven   
55    10455.0          Bronx     Hunts Point and Mott Haven   
56    10456.0          Bronx     High Bridge and Morrisania   
57    10457.0          Bronx                  Central Bronx   
58    10458.0          Bronx         Bronx Park and Fordham   
59    10459.0          Bronx     Hunts Point and Mott Haven   
60    10460.0          Bronx                  Central Bronx   
61    10461.0          Bronx                Southeast Bronx   
62    10462.0          Bronx        

# Final table

In [79]:
neighborhoods_venues_sorted.dtypes

ZIPCODES                  float64
Borough                    object
Neighborhoods              object
1st Most Common Venue      object
2nd Most Common Venue      object
3rd Most Common Venue      object
4th Most Common Venue      object
5th Most Common Venue      object
6th Most Common Venue      object
7th Most Common Venue      object
8th Most Common Venue      object
9th Most Common Venue      object
10th Most Common Venue     object
dtype: object

In [81]:
#Add corona cases and population density to the above table
nycmain = pd.merge(NYCCOR, neighborhoods_venues_sorted, on='ZIPCODES')
nycmain

Borough_x                   Neighborhood  ZIPCODES  Positive    pkm  \
0            Bronx                  Central Bronx   10453.0      1547  34653   
1            Bronx                  Central Bronx   10457.0      1362  34653   
2            Bronx                  Central Bronx   10460.0      1097  34653   
3            Bronx         Bronx Park and Fordham   10458.0      1342  34653   
4            Bronx         Bronx Park and Fordham   10467.0      2372  34653   
5            Bronx         Bronx Park and Fordham   10468.0      1666  34653   
6            Bronx     High Bridge and Morrisania   10451.0      1108  34653   
7            Bronx     High Bridge and Morrisania   10452.0      1488  34653   
8            Bronx     High Bridge and Morrisania   10456.0      1596  34653   
9            Bronx     Hunts Point and Mott Haven   10454.0       747  34653   
10           Bronx     Hunts Point and Mott Haven   10455.0       831  34653   
11           Bronx     Hunts Point and Mott Haven   10459.0       996  34653   
12           Bronx     Hunts Point and Mott Haven   10474.0       230  34653   
13           Bronx      Kingsbridge and Riverdale   10463.0      1261  34653   
14           Bronx      Kingsbridge and Riverdale   10471.0       414  34653   
15           Bronx                Northeast Bronx   10466.0      1727  34653   
16           Bronx                Northeast Bronx   10469.0      2131  34653   
17           Bronx                Northeast Bronx   10470.0       336  34653   
18           Bronx                Northeast Bronx   10475.0      1285  34653   
19           Bronx                Southeast Bronx   10461.0      1328  34653   
20           Bronx                Southeast Bronx   10462.0      1611  34653   
21           Bronx                Southeast Bronx   10464.0       103  34653   
22           Bronx                Southeast Bronx   10465.0      1128  34653   
23           Bronx                Southeast Bronx   10472.0      1287  34653   
24           Bronx                Southeast Bronx   10473.0      1371  34653   
25        Brooklyn               Central Brooklyn   11212.0      1134  37137   
26        Brooklyn               Central Brooklyn   11213.0      1010  37137   
27        Brooklyn               Central Brooklyn   11216.0       500  37137   
28        Brooklyn               Central Brooklyn   11233.0       844  37137   
29        Brooklyn               Central Brooklyn   11238.0       547  37137   
30        Brooklyn             Southwest Brooklyn   11209.0       800  37137   
31        Brooklyn             Southwest Brooklyn   11214.0      1050  37137   
32        Brooklyn             Southwest Brooklyn   11228.0       470  37137   
33        Brooklyn                   Borough Park   11204.0      1358  37137   
34        Brooklyn                   Borough Park   11218.0      1192  37137   
35        Brooklyn                   Borough Park   11219.0      1988  37137   
36        Brooklyn                   Borough Park   11230.0      1620  37137   
37        Brooklyn         Canarsie and Flatlands   11234.0      1670  37137   
38        Brooklyn         Canarsie and Flatlands   11236.0      1899  37137   
39        Brooklyn         Canarsie and Flatlands   11239.0       354  37137   
40        Brooklyn              Southern Brooklyn   11223.0      1171  37137   
41        Brooklyn              Southern Brooklyn   11224.0       695  37137   
42        Brooklyn              Southern Brooklyn   11229.0      1110  37137   
43        Brooklyn              Southern Brooklyn   11235.0      1343  37137   
44        Brooklyn             Northwest Brooklyn   11201.0       460  37137   
45        Brooklyn             Northwest Brooklyn   11205.0       490  37137   
46        Brooklyn             Northwest Brooklyn   11215.0       453  37137   
47        Brooklyn             Northwest Brooklyn   11217.0       411  37137   
48        Brooklyn             Northwest Brooklyn   11231.0       303  37137   
49       

In [84]:
# sort by positive number of cases
nycmain.sort_values(["Positive"], ascending=False, inplace=True)
nycmain

Borough_x                   Neighborhood  ZIPCODES  Positive    pkm  \
152         Queens                    West Queens   11368.0      2919  21460   
4            Bronx         Bronx Park and Fordham   10467.0      2372  34653   
156         Queens                    West Queens   11373.0      2269  21460   
16           Bronx                Northeast Bronx   10469.0      2131  34653   
170  Staten Island                     Mid-Island   10314.0      2030   8112   
35        Brooklyn                   Borough Park   11219.0      1988  37137   
38        Brooklyn         Canarsie and Flatlands   11236.0      1899  37137   
155         Queens                    West Queens   11372.0      1764  21460   
15           Bronx                Northeast Bronx   10466.0      1727  34653   
37        Brooklyn         Canarsie and Flatlands   11234.0      1670  37137   
5            Bronx         Bronx Park and Fordham   10468.0      1666  34653   
36        Brooklyn                   Borough Park   11230.0      1620  37137   
20           Bronx                Southeast Bronx   10462.0      1611  34653   
8            Bronx     High Bridge and Morrisania   10456.0      1596  34653   
0            Bronx                  Central Bronx   10453.0      1547  34653   
131         Queens                      Rockaways   11691.0      1543  21460   
7            Bronx     High Bridge and Morrisania   10452.0      1488  34653   
54        Brooklyn     East New York and New Lots   11208.0      1463  37137   
157         Queens                    West Queens   11377.0      1448  21460   
55        Brooklyn                     Greenpoint   11211.0      1422  37137   
118         Queens                        Jamaica   11434.0      1415  21460   
52        Brooklyn                       Flatbush   11226.0      1413  37137   
130         Queens            West Central Queens   11385.0      1396  21460   
49        Brooklyn                       Flatbush   11203.0      1385  37137   
24           Bronx                Southeast Bronx   10473.0      1371  34653   
1            Bronx                  Central Bronx   10457.0      1362  34653   
33        Brooklyn                   Borough Park   11204.0      1358  37137   
43        Brooklyn              Southern Brooklyn   11235.0      1343  37137   
3            Bronx         Bronx Park and Fordham   10458.0      1342  34653   
19           Bronx                Southeast Bronx   10461.0      1328  34653   
53        Brooklyn     East New York and New Lots   11207.0      1306  37137   
23           Bronx                Southeast Bronx   10472.0      1287  34653   
18           Bronx                Northeast Bronx   10475.0      1285  34653   
13           Bronx      Kingsbridge and Riverdale   10463.0      1261  34653   
166  Staten Island                    South Shore   10312.0      1224   8112   
50        Brooklyn                       Flatbush   11210.0      1219  37137   
72       Manhattan                    East Harlem   10029.0      1202  72033   
34        Brooklyn                   Borough Park   11218.0      1192  37137   
40        Brooklyn              Southern Brooklyn   11223.0      1171  37137   
128         Queens            West Central Queens   11375.0      1170  21460   
25        Brooklyn               Central Brooklyn   11212.0      1134  37137   
116         Queens                        Jamaica   11432.0      1133  21460   
22           Bronx                Southeast Bronx   10465.0      1128  34653   
162  Staten Island                    South Shore   10306.0      1124   8112   
42        Brooklyn              Southern Brooklyn   11229.0      1110  37137   
6            Bronx     High Bridge and Morrisania   10451.0      1108  34653   
2            Bronx                  Central Bronx   10460.0      1097  34653   
153         Queens                    West Queens   11369.0      1081  21460   
119         Queens                        Jamaica   11435.0      1057  21460   
31       

In [85]:
nycmain.columns

Index(['Borough_x', 'Neighborhood', 'ZIPCODES', 'Positive', 'pkm', 'pmi',
       'lat', 'long', 'Borough_y', 'Neighborhoods', '1st Most Common Venue',
       '2nd Most Common Venue', '3rd Most Common Venue',
       '4th Most Common Venue', '5th Most Common Venue',
       '6th Most Common Venue', '7th Most Common Venue',
       '8th Most Common Venue', '9th Most Common Venue',
       '10th Most Common Venue'],
      dtype='object')

In [86]:
nycmain = nycmain.drop(columns=['ZIPCODES', 'pmi', 'lat', 'long', '6th Most Common Venue', '7th Most Common Venue',
       '8th Most Common Venue', '9th Most Common Venue',
       '10th Most Common Venue'])
nycmain

Borough_x                   Neighborhood  Positive    pkm  \
152         Queens                    West Queens      2919  21460   
4            Bronx         Bronx Park and Fordham      2372  34653   
156         Queens                    West Queens      2269  21460   
16           Bronx                Northeast Bronx      2131  34653   
170  Staten Island                     Mid-Island      2030   8112   
35        Brooklyn                   Borough Park      1988  37137   
38        Brooklyn         Canarsie and Flatlands      1899  37137   
155         Queens                    West Queens      1764  21460   
15           Bronx                Northeast Bronx      1727  34653   
37        Brooklyn         Canarsie and Flatlands      1670  37137   
5            Bronx         Bronx Park and Fordham      1666  34653   
36        Brooklyn                   Borough Park      1620  37137   
20           Bronx                Southeast Bronx      1611  34653   
8            Bronx     High Bridge and Morrisania      1596  34653   
0            Bronx                  Central Bronx      1547  34653   
131         Queens                      Rockaways      1543  21460   
7            Bronx     High Bridge and Morrisania      1488  34653   
54        Brooklyn     East New York and New Lots      1463  37137   
157         Queens                    West Queens      1448  21460   
55        Brooklyn                     Greenpoint      1422  37137   
118         Queens                        Jamaica      1415  21460   
52        Brooklyn                       Flatbush      1413  37137   
130         Queens            West Central Queens      1396  21460   
49        Brooklyn                       Flatbush      1385  37137   
24           Bronx                Southeast Bronx      1371  34653   
1            Bronx                  Central Bronx      1362  34653   
33        Brooklyn                   Borough Park      1358  37137   
43        Brooklyn              Southern Brooklyn      1343  37137   
3            Bronx         Bronx Park and Fordham      1342  34653   
19           Bronx                Southeast Bronx      1328  34653   
53        Brooklyn     East New York and New Lots      1306  37137   
23           Bronx                Southeast Bronx      1287  34653   
18           Bronx                Northeast Bronx      1285  34653   
13           Bronx      Kingsbridge and Riverdale      1261  34653   
166  Staten Island                    South Shore      1224   8112   
50        Brooklyn                       Flatbush      1219  37137   
72       Manhattan                    East Harlem      1202  72033   
34        Brooklyn                   Borough Park      1192  37137   
40        Brooklyn              Southern Brooklyn      1171  37137   
128         Queens            West Central Queens      1170  21460   
25        Brooklyn               Central Brooklyn      1134  37137   
116         Queens                        Jamaica      1133  21460   
22           Bronx                Southeast Bronx      1128  34653   
162  Staten Island                    South Shore      1124   8112   
42        Brooklyn              Southern Brooklyn      1110  37137   
6            Bronx     High Bridge and Morrisania      1108  34653   
2            Bronx                  Central Bronx      1097  34653   
153         Queens                    West Queens      1081  21460   
119         Queens                        Jamaica      1057  21460   
31        Brooklyn             Southwest Brooklyn      1050  37137   
154         Queens                    West Queens      1037  21460   
168  Staten Island       Stapleton and St. George      1035   8112   
57        Brooklyn                    Sunset Park      1025  37137   
59        Brooklyn      Bushwick and Williamsburg      1013  37137   
26        Brooklyn               Central Brooklyn      1010  37137   
11           Bronx     Hunts Point and Mott Haven       996  34653   
97       Manhattan 

# THE END